In [268]:
##########define states and constants########
gamma = 0.95

#variable 1
grid_length = 20

#variable 2
gas_level_interval = 0.1
num_gas_level_intervals = int(1 / gas_level_interval)

#variable 3
gas_station_present = 2

#variable 4
gas_price_max = 4.00
gas_price_min = 3.00
gas_price_interval = 0.10
num_gas_price_intervals = int((gas_price_max - gas_price_min) / gas_price_interval)

total_num_states = grid_length * grid_length * num_gas_level_intervals 

##########define actions########

#move left, right, up, down
num_moves = 4
#pump or not pump
pump_or_not = 1

total_actions = num_moves + pump_or_not

#########initialization########

#create a 4d matrix, change it to sparse matrix
R = zeros(grid_length,grid_length,num_gas_level_intervals, total_actions)

#randomly pick starting point
start_pt = (int(rand() * grid_length) , int(rand() * grid_length))

#randomly pick ending point
end_pt = (int(rand() * grid_length) , int(rand() * grid_length))
println("end: ", end_pt)

#randomly intialize gas stations
num_gas_stations = 10
station_set = Set()
for i = 1:num_gas_stations
    station_pt = (int(rand() * grid_length) , int(rand() * grid_length))
    push!(station_set,station_pt)
#     while !in( station_pt, station_pt)
#         station_pt = (int(rand() * grid_length) , int(rand() * grid_length))
#         push!(station_set,station_pt)
#     end
end
println("gas: ", station_set)


########initialize rewards#######

#initialize destination reward
destination_default_reward = 3000
dest_offset = 500
for i = 1:num_gas_level_intervals
    gas_level = (i / num_gas_level_intervals)
    R[end_pt[1],end_pt[2],i,:] = destination_default_reward + dest_offset * gas_level
end

#initialize deadend reward
dead_end_reward = -1500
R[:,:, 1,:] = dead_end_reward
#edge case - ensure u can finsih at end point with 0 gas left
gas_level = (1 / num_gas_level_intervals)
R[end_pt[1],end_pt[2],1,:] = destination_default_reward + dest_offset * gas_level

#initialize refuelling reward
refuel_default_reward = 1500
for i = 1:num_gas_level_intervals
#     for j = 1:num_gas_price_intervals
        gas_level = (i / num_gas_level_intervals)
#         curr_price = gas_price_min + (j / num_gas_price_intervals) * (gas_price_max - gas_price_min)
        #action 5 is refuel, 1 means gas station is present
        for pt in station_set
            curr_price = int(rand() * num_gas_price_intervals + 1)
#             R[pt[1],pt[2],i,5] = refuel_default_reward * (1 - gas_level) / curr_price
            R[pt[1],pt[2],i,5] = refuel_default_reward * (1 - gas_level) 
            #if gas is already full, why fill it again?
            if gas_level == 1
                R[pt[1],pt[2],i,5] = -50
            end
        end
#         R[:,:,i,1,j,5] = refuel_default_reward * (1 - gas_level) / curr_price
#         #if gas is already full, why fill it again?
#         if gas_level == 1
#             R[:,:,i,1,j,5] = -100
#         end
#     end
end


end: (18,5)
gas: Set{Any}({(5,17),(14,10),(19,18),(7,18),(13,8),(5,1),(10,4),(2,14),(13,4),(12,6)})


In [269]:
#########define transtion functions##########

function get_next_states(x, y, glevel, a)
    
    next_state_array = Tuple[]
    
    #move up down left right
    if a == 1 && x + 1 <= grid_length && glevel - 1 >= 1
        push!(next_state_array, (x + 1, y, glevel - 1))
    end
    
    if a == 2 && x - 1 >= 1 && glevel - 1 >= 1
        push!(next_state_array, (x - 1, y, glevel - 1))
    end
    
    if a == 3 && y + 1 <= grid_length && glevel - 1 >= 1
        push!(next_state_array, (x, y + 1, glevel - 1))
    end
    
    if a == 4 && y - 1 >= 1 && glevel - 1 >= 1
        push!(next_state_array, (x, y - 1, glevel - 1))
    end
    
    #topping up gas
    if a == 5 && in((x,y), station_set)
        push!(next_state_array, (x, y, num_gas_level_intervals))
    end
    
#     println((x, y, 1, gas_station_present,num_gas_price_intervals))
    
    return next_state_array
end


get_next_states (generic function with 1 method)

In [270]:
#find all the reachable states from start state
tic()
U = zeros(grid_length,grid_length,num_gas_level_intervals)
A = zeros(grid_length,grid_length,num_gas_level_intervals)
for k = 1:400
    old_u = deepcopy(U)
    for i = 1:grid_length
        for j = 1:grid_length
            for glevel = 1:num_gas_level_intervals
                U_max = -99999
                for a = 1:total_actions
                    if a == 5 && !in ((i,j), station_set)
                        continue
                    end
                    next_states_array = get_next_states(i,j,glevel,a)
                    accum_reward = 0
                    for s in next_states_array
                        accum_reward += U[s[1],s[2],s[3]]
                    end
#                     println(accum_reward, "***", next_states_array)
                    curr_u = R[i,j,glevel,a] + gamma * accum_reward
                    if curr_u > U_max
                        U_max = curr_u
                        A[i,j,glevel] = a
                    end
                end
                U[i,j,glevel] = U_max
#                 println(U_max)
            end
        end
#         if i%51 == 0
#             println("halfway")
#         end
    end
    if norm(vec(U)-vec(old_u)) < 0.1
#         println(vec(U))
#         println("-----------------------------------------------------------------------------------------------")
#         println(vec(old_u))
        println("converged at: ", k, " iters")
        break
    end
    println("k: ",k)
end
toc()

k: 1
k: 2
k: 3
k: 4
k: 5
k: 6
k: 7
k: 8
k: 9
k: 10
k: 11
k: 12
k: 13
k: 14
k: 15
k: 16
k: 17
k: 18
k: 19
k: 20
k: 21
k: 22
k: 23
k: 24
k: 25
k: 26
k: 27
k: 28
k: 29
k: 30
k: 31
k: 32
k: 33
k: 34
k: 35
k: 36
k: 37
k: 38
k: 39
k: 40
k: 41
k: 42
k: 43
k: 44
k: 45
k: 46
k: 47
k: 48
k: 49
k: 50
k: 51
k: 52
k: 53
k: 54
k: 55
k: 56
k: 57
k: 58
k: 59
k: 60
k: 61
k: 62
k: 63
k: 64
k: 65
k: 66
k: 67
k: 68
k: 69
k: 70
k: 71
k: 72
k: 73
k: 74
k: 75
k: 76
k: 77
k: 78
k: 79
k: 80
k: 81
k: 82
k: 83
k: 84
k: 85
k: 86
k: 87
k: 88
k: 89
k: 90
k: 91
k: 92
k: 93
k: 94
k: 95
k: 96
k: 97
k: 98
k: 99
k: 100
k: 101
k: 102
k: 103
k: 104
k: 105
k: 106
k: 107
k: 108
k: 109
k: 110
k: 111
k: 112
k: 113
k: 114
k: 115
k: 116
k: 117
k: 118
k: 119
k: 120
k: 121
k: 122
converged at: 123 iters
elapsed time: 1.735543886 seconds


1.735543886

In [ ]:
(grid_length,grid_length,num_gas_level_intervals,gas_station_present,num_gas_price_intervals, total_actions), total_num_states

In [ ]:
#begin value iteration

In [ ]:
println(end_pt[1]," ",end_pt[2])
f = open("/Users/yishh/Box Sync/CS 238/project_stuff/proj_utility_output_1.csv","w")
a_f = open("/Users/yishh/Box Sync/CS 238/project_stuff/proj_actions_output_1.csv","w")
for i = 1:grid_length
    for j = 1:grid_length
        #get the max of each x,y coordinate
        #find the action
#         print(maximum(U[i,j,:,:,:]), " ")
#         write(f, string(round(maximum(U[i,j,:]),1)) ,"-", string(indmax(U[i,j,:])))
         write(f, string(round(maximum(U[i,j,:]),1)) )
        write(f, "\t")
        write(a_f, string(int(A[i,j,:][indmax(U[i,j,:])])))
        write(a_f, "\t")
    end
#     println("")
    write(f, "\n")
    write(a_f, "\n")
end
close(f)
close(a_f)

In [ ]:
println(end_pt[1]," ",end_pt[2])
f = open("/Users/yishh/Box Sync/CS 238/project_stuff/proj_utility_output_1.csv","w")
a_f = open("/Users/yishh/Box Sync/CS 238/project_stuff/proj_actions_output_1.csv","w")
for i = 1:grid_length
    if i ==1
        write(f, "\[")
    end
    write(f, "\[")
    for j = 1:grid_length
        #get the max of each x,y coordinate
        #find the action
#         print(maximum(U[i,j,:,:,:]), " ")
#         write(f, string(round(maximum(U[i,j,:]),1)) ,"-", string(indmax(U[i,j,:])))

        write(f, string(round(maximum(U[j,i,:]),1)) )
        if j != grid_length
            write(f, ", ")
        end
        write(a_f, string(int(A[i,j,:][indmax(U[i,j,:])])))
        write(a_f, "\t")
    end
    write(f, "\]")
#     println("")
    write(f, ",\n")
    write(a_f, "\n")
    if i == grid_length
        write(f, "\]")
    end
end
close(f)
close(a_f)

In [271]:
for stn in station_set
    println(stn, ",")
end

(5,17),
(14,10),
(19,18),
(7,18),
(13,8),
(5,1),
(10,4),
(2,14),
(13,4),
(12,6),


In [272]:
function bfs(x,y)
    path = Tuple[]
    push!(path,(x,y))
    first_action = A[x,y,10]
#     println("start: ", x ," , ", y)
    next_state = get_next_state(x,y,10,first_action)
#     println( next_state)
    push!(path,(next_state[1],next_state[2]))
    for i = 1:1000
        next_state = get_next_state(next_state[1],next_state[2],next_state[3],A[next_state[1],next_state[2],next_state[3]])
        
        println(next_state, "   U: ", U[next_state[1], next_state[2],next_state[3]], "    a: ", A[next_state[1],next_state[2],next_state[3]])
        push!(path,(next_state[1],next_state[2]))
        if (next_state[1],next_state[2]) == end_pt
            println("reached goal in :" , i+2)
#             push!(path,(next_state[1],next_state[2]))
            break
        end
    end
    return path
end

bfs (generic function with 1 method)

In [273]:
# A[34,4,10]
tic()
println("destination: ", end_pt)
path = bfs(5,20)
println(length(path))
toc()

destination: (18,5)
(7,20,8)   U: 2430.02890139486    a: 1.0
(8,20,7)   U: 2557.926975230636    a: 2.0
(7,20,6)   U: 2692.5547107690904    a: 4.0
(7,19,5)   U: 2834.2681165990425    a: 4.0
(7,18,4)   U: 2983.4401227358344    a: 5.0
(7,18,10)   U: 2193.09699630305    a: 1.0
(8,18,9)   U: 2308.525484742097    a: 1.0
(9,18,8)   U: 2430.02890139486    a: 1.0
(10,18,7)   U: 2557.926975230636    a: 2.0
(9,18,6)   U: 2692.5547107690904    a: 2.0
(8,18,5)   U: 2834.2681165990425    a: 2.0
(7,18,4)   U: 2983.4401227358344    a: 5.0
(7,18,10)   U: 2193.09699630305    a: 1.0
(8,18,9)   U: 2308.525484742097    a: 1.0
(9,18,8)   U: 2430.02890139486    a: 1.0
(10,18,7)   U: 2557.926975230636    a: 2.0
(9,18,6)   U: 2692.5547107690904    a: 2.0
(8,18,5)   U: 2834.2681165990425    a: 2.0
(7,18,4)   U: 2983.4401227358344    a: 5.0
(7,18,10)   U: 2193.09699630305    a: 1.0
(8,18,9)   U: 2308.525484742097    a: 1.0
(9,18,8)   U: 2430.02890139486    a: 1.0
(10,18,7)   U: 2557.926975230636    a: 2.0
(9,18,

0.110520703

In [274]:
#########define transtion functions##########

function get_next_state(x, y, glevel, a)
    
    next_state_array = Tuple[]
    
    #move up down left right
    if a == 1 && x + 1 <= grid_length && glevel - 1 >= 1
        return (x + 1, y, glevel - 1)
    end
    
    if a == 2 && x - 1 >= 1 && glevel - 1 >= 1
        return x - 1, y, glevel - 1
    end
    
    if a == 3 && y + 1 <= grid_length && glevel - 1 >= 1
        return x, y + 1, glevel - 1
    end
    
    if a == 4 && y - 1 >= 1 && glevel - 1 >= 1
        return x, y - 1, glevel - 1
    end
    
    #topping up gas
    if a == 5 && in((x,y), station_set)
        return x, y, num_gas_level_intervals
    end
    
#     println((x, y, 1, gas_station_present,num_gas_price_intervals))
    return 0
    return next_state_array
end


get_next_state (generic function with 1 method)

In [275]:
for xy in path
    println(xy, ",")
end

(5,20),
(6,20),
(7,20),
(8,20),
(7,20),
(7,19),
(7,18),
(7,18),
(8,18),
(9,18),
(10,18),
(9,18),
(8,18),
(7,18),
(7,18),
(8,18),
(9,18),
(10,18),
(9,18),
(8,18),
(7,18),
(7,18),
(8,18),
(9,18),
(10,18),
(9,18),
(8,18),
(7,18),
(7,18),
(8,18),
(9,18),
(10,18),
(9,18),
(8,18),
(7,18),
(7,18),
(8,18),
(9,18),
(10,18),
(9,18),
(8,18),
(7,18),
(7,18),
(8,18),
(9,18),
(10,18),
(9,18),
(8,18),
(7,18),
(7,18),
(8,18),
(9,18),
(10,18),
(9,18),
(8,18),
(7,18),
(7,18),
(8,18),
(9,18),
(10,18),
(9,18),
(8,18),
(7,18),
(7,18),
(8,18),
(9,18),
(10,18),
(9,18),
(8,18),
(7,18),
(7,18),
(8,18),
(9,18),
(10,18),
(9,18),
(8,18),
(7,18),
(7,18),
(8,18),
(9,18),
(10,18),
(9,18),
(8,18),
(7,18),
(7,18),
(8,18),
(9,18),
(10,18),
(9,18),
(8,18),
(7,18),
(7,18),
(8,18),
(9,18),
(10,18),
(9,18),
(8,18),
(7,18),
(7,18),
(8,18),
(9,18),
(10,18),
(9,18),
(8,18),
(7,18),
(7,18),
(8,18),
(9,18),
(10,18),
(9,18),
(8,18),
(7,18),
(7,18),
(8,18),
(9,18),
(10,18),
(9,18),
(8,18),
(7,18),
(7,18),
(8,18),
(9,18),
(10,18),

In [276]:
pts_array = Tuple[]
for i = 1:grid_length
    for j = 1:grid_length
        curr_max_u = round(maximum(U[i,j,:]),1)
        p = bfs(i,j)
        p_length = -1
        if length(p) == 1002
            p_length = -1
        else
            p_length = length(p)
        end
        curr = (curr_max_u,p_length)
        push!(pts_array,curr)
    end
end
        

(3,1,8)   U: 3211.637826710457    a: 1.0
(4,1,7)   U: 3380.6713965373233    a: 1.0
(5,1,6)   U: 3558.601470039288    a: 5.0
(5,1,10)   U: 3114.317336883461    a: 1.0
(6,1,9)   U: 3278.228775666801    a: 1.0
(7,1,8)   U: 3450.7671322808433    a: 1.0
(8,1,7)   U: 3632.386455032467    a: 1.0
(9,1,6)   U: 3823.5646895078603    a: 1.0
(10,1,5)   U: 4024.8049363240634    a: 3.0
(10,2,4)   U: 4236.636775077962    a: 3.0
(10,3,3)   U: 4459.617657976803    a: 3.0
(10,4,2)   U: 4694.334376817687    a: 5.0
(10,4,10)   U: 3678.246712439671    a: 1.0
(11,4,9)   U: 3871.838644673338    a: 1.0
(12,4,8)   U: 4075.619625971935    a: 3.0
(12,5,7)   U: 4290.125922075721    a: 3.0
(12,6,6)   U: 4515.922023237601    a: 5.0
(12,6,10)   U: 4122.0231823553695    a: 1.0
(13,6,9)   U: 4338.971770900389    a: 1.0
(14,6,8)   U: 4567.338706210936    a: 1.0
(15,6,7)   U: 4807.724953906249    a: 1.0
(16,6,6)   U: 5060.763109374999    a: 1.0
(17,6,5)   U: 5327.119062499999    a: 1.0
(18,6,4)   U: 5607.49375    a: 4.0

In [277]:
pts_array

400-element Array{(Any...,),1}:
 (3509.4,27)
 (3333.9,28)
 (3167.2,29)
 (3053.1,23)
 (2858.4,31)
 (2715.5,32)
 (2277.8,-1)
 (2397.7,-1)
 (2523.9,-1)
 (2656.7,-1)
 (2796.5,-1)
 (2943.7,-1)
 (3098.7,-1)
 ⋮          
 (4339.0,7) 
 (4122.0,8) 
 (3291.4,23)
 (3126.8,24)
 (2970.5,25)
 (2656.7,-1)
 (2796.5,-1)
 (2943.7,-1)
 (3098.7,-1)
 (3261.8,-1)
 (3098.7,-1)
 (2943.7,-1)

In [279]:
for p in pts_array
    println(p, ",") 
end

(3509.4,27),
(3333.9,28),
(3167.2,29),
(3053.1,23),
(2858.4,31),
(2715.5,32),
(2277.8,-1),
(2397.7,-1),
(2523.9,-1),
(2656.7,-1),
(2796.5,-1),
(2943.7,-1),
(3098.7,-1),
(3261.8,-1),
(3098.7,-1),
(2943.7,-1),
(2796.5,-1),
(2656.7,-1),
(2523.9,-1),
(2397.7,-1),
(3694.1,26),
(3509.4,27),
(3333.9,23),
(3213.8,22),
(3053.1,23),
(2858.4,31),
(2715.5,32),
(2523.9,-1),
(2656.7,-1),
(2796.5,-1),
(2943.7,-1),
(3098.7,-1),
(3261.8,-1),
(3433.4,-1),
(3261.8,-1),
(3098.7,-1),
(2943.7,-1),
(2796.5,-1),
(2656.7,-1),
(2523.9,-1),
(3888.5,25),
(3694.1,23),
(3509.4,22),
(3383.0,21),
(3213.8,22),
(3318.8,18),
(2858.4,31),
(2715.5,32),
(2523.9,-1),
(2656.7,-1),
(2796.5,-1),
(2943.7,-1),
(3098.7,-1),
(3261.8,-1),
(3098.7,-1),
(2943.7,-1),
(3098.7,-1),
(2943.7,-1),
(2796.6,-1),
(2656.7,-1),
(4093.2,23),
(3888.5,22),
(3694.1,21),
(3561.0,20),
(3383.0,18),
(3493.5,17),
(3318.8,18),
(3092.0,22),
(2715.5,32),
(2523.9,-1),
(2656.7,-1),
(2796.5,-1),
(2943.7,-1),
(3098.7,-1),
(2943.7,-1),
(3098.7,-1),
(3261.8,-1),